## Processing Data 
We want to get the data containing coordinates and document counts from the specified url and format it appropriately. 

We first load the data from the URL into a pandas DataFrame. 

In [1]:
import pandas as pd 
import numpy as np 
import geopandas as gpd 
from shapely.geometry import Polygon
import folium
import math 
import pyproj

url="http://ads.directlyapply.com/sample/shipt"
data  = pd.read_json(url)
data.loc[1]['tags']


{'doc_count_error_upper_bound': 0,
 'sum_other_doc_count': 0,
 'buckets': [{'key': '21.907399990595877,-159.58320007659495',
   'doc_count': 25},
  {'key': '21.90829999744892,-159.47490002028644', 'doc_count': 25},
  {'key': '21.91534398123622,-159.58703219890594', 'doc_count': 25},
  {'key': '21.925899982452393,-159.53030004166067', 'doc_count': 25},
  {'key': '21.930899997241795,-159.49930007569492', 'doc_count': 25}]}

We see that the data lat/lon data is contained within the tags section. We want to extract this out into a seprate dataframe for processing. 

We first convert the 'tags' column to a list of dictionary objects. 

In [2]:
data = data['tags'].to_list()


We then process the 'buckets' dictionary section, which contains the relevant data. We first convert this into a numpy array and then flatten it. Finally we extract the lat,lon and document counts into seperate arrays. 

In [3]:

keys = np.array([np.array(x['buckets'],dtype=object) for x in data ],dtype=object)
k = np.concatenate(keys)
locs = np.array([x.get('key').split(',') for x in k])
doc_count = [x.get('doc_count') for x in k ]
lat = [x[0] for x in locs]
lon = [x[1] for x in locs]


Lastly we input the values into a new dataframe. 

In [4]:
d = {'lat':lat,'lon':lon,'count':doc_count}
locations = pd.DataFrame(data=d)
locations['lat'] = locations['lat'].astype(np.float64)
locations['lon'] = locations['lon'].astype(np.float64)
locations.head()

lat         lon  count
0  21.921300 -159.624100     25
1  21.957100 -159.668900     25
2  21.907400 -159.583200     25
3  21.908300 -159.474900     25
4  21.915344 -159.587032     25

## Problem Approach 

We now have a list of coordinates along with the the document counts at each location.

The assignment states that we want to apply the smallest circle problem to all points within a 30 mile bounding box. So we can take the following approach.

* We first get a bounding box which contains all the points in our DataFrame. We ensure this box is a square which has a length that is a multiple of 30.

* We turn this bounding box into a grid of smaller bounding boxes each with dimensions of $30 \times 30$ miles.

* For each of these grid boxes we apply the apply the smallest circle problem to all the points contained within it. 


### Compute Bounding Box for overall data

We will first create the bounding box which contains all the points in our Data Frame. We can use geopandas to easily calculate the bounds of our coordinates. We use the ESPG:4326 coordinate systme which corresponds to lat/lon.

We first convert our locations to a GeoDataFrame. 
We then create a polygon shape which edges connects all the seperate points.
We take the [envelope](https://geopandas.org/en/stable/docs/reference/api/geopandas.GeoSeries.envelope.html) of the polygon to get the entire region over which our coordinates range over as a rectangle.



In [5]:
locations = gpd.GeoDataFrame(locations,crs="EPSG:4326",geometry=gpd.points_from_xy(locations.lon, locations.lat) )

poly_geom = Polygon(zip(locations['lon'].to_list(),locations['lat'].to_list()))
poly_envelope = poly_geom.envelope
polygon = gpd.GeoDataFrame(index=[0], crs='epsg:4326', geometry=[poly_geom])
envelope = gpd.GeoDataFrame(index=[0], crs='epsg:4326', geometry=[poly_envelope]) 


In [6]:
map = folium.Map(location = [locations.loc[0]['lat'], locations.loc[0]['lon']], tiles='cartodbdark_matter' , zoom_start = 2)
folium.GeoJson(envelope).add_to(map)

map

### Convert bounding box into grid

We have ommited this part for now due to time constraints. The general procedure would be as follows. 

* Starting at the top right corner iteratively create a polygon from left to right, incrementing the latitude until we reach the end of the shape

* Restart the algorithm by setting the latitude to maximum but increment the longitude by 30 

* Continue until entire box has been covered 

An important point to note is that we would either use the haversine formula or geopandas inbuilt libraries to calculate how a 30 mile change would be reflected in latitude/Longitude. 

### Smallest Circle Problem 

We now have  $ 30 \times 30$ grids, each containing varying number of lat/lon points with corresponding document counts. 

Before we apply the Smallest Circle Formulation, it is important to point out a limitation of our current approach. Consider the image below 

![img](./SquareCircle.png)

Under our current formulation of solving the bounding box within a circle any points occuring within the red square will not be included in the solution. Given that we will solve the problem for all points in the 30 mile bounding box, the produced circle may be bigger than our 30 mile bounding box. For now we will go ahead with solving the smallest circle problem and tackle this problem at a later point. 

We will simulate what the input bounding box would look like if it was calculated in the previous section. First lets add all our locations to the map. 

In [7]:

for x in locations.index:
    folium.CircleMarker(
                location=[locations['lat'][x], locations['lon'][x]],
                popup=locations['count'][x],
                radius = 1
                ).add_to(map)
folium.LatLngPopup().add_to(map)

map

Next we want to simulate one of the smaller bounding boxes. We will pick an arbitrary area in washington with high density of points. 

In [8]:

lonList = [-77.6312,-76.8240,-76.7911,-77.4939]
latList = [39.0660,39.0703,38.7798,38.7883]
  
polygon_geom = Polygon(zip(lonList, latList))
polygon = gpd.GeoDataFrame(index=[0], crs='epsg:4326', geometry=[polygon_geom])      
    

poly_envelope = polygon_geom.envelope

e = gpd.GeoDataFrame(index=[0], crs='epsg:4326', geometry=[poly_envelope]) 

map = folium.Map(location = [38.9170, -77.0505], tiles='cartodbdark_matter' , zoom_start = 10)
folium.GeoJson(e).add_to(map)
map



We can filter our locations to capture points that occur in the bounding box and plot them in the box.



In [9]:
mask = locations.apply( lambda x: poly_envelope.contains(x.geometry),axis =1 )
locationsInBox = locations[mask]
for x in locationsInBox.index:
    folium.CircleMarker(
                location=[locations['lat'][x], locations['lon'][x]],
                popup=locations['count'][x],
                radius = 1
                ).add_to(map)
folium.LatLngPopup().add_to(map)


map

We now have a set of points to solve the smallest circle problem over. We can move onto developing an efficient approach to solving the problem. 

Geopandas has efficient libraries for computing the convex hull of a set of points. A convex hull is the smallest set that contains all of our points. 

lets see what that looks like for our set of points. 



In [10]:
map = folium.Map(location = [38.9170, -77.0505], tiles='cartodbdark_matter' , zoom_start = 10)

poly_geom = Polygon(zip(locationsInBox['lon'].to_list(),locationsInBox['lat'].to_list()))
poly_hull = poly_geom.convex_hull
hull = gpd.GeoDataFrame(index=[0], crs='epsg:4326', geometry=[poly_hull]) 
folium.GeoJson(hull).add_to(map)

for x in locationsInBox.index:
    folium.CircleMarker(
                location=[locations['lat'][x], locations['lon'][x]],
                popup=locations['count'][x],
                radius = 1
                ).add_to(map)
map

Notice that there are certain points that lie on the edge of the convex set. We can measure the distance from the center of the convex set to all of these points. We can then take the longest of these distances and make it the radius of the circle in the center. This transformation will allow us to easily calculate the smallest circle that contains all of the points. 

In [11]:
poly_hull.boundary

mask = locationsInBox.apply( lambda x: poly_hull.boundary.contains(x.geometry),axis =1 )

pointsOnEdge = locationsInBox[mask]
pointsOnEdge

lat        lon  count                    geometry
2896  39.066800 -76.996900      2  POINT (-76.99690 39.06680)
2955  38.976600 -76.805300     25  POINT (-76.80530 38.97660)
3013  38.791200 -77.081400      1  POINT (-77.08140 38.79120)
3024  38.815700 -77.621600     25  POINT (-77.62160 38.81570)
3026  38.785562 -77.527546     11  POINT (-77.52755 38.78556)
3037  39.049900 -76.834500      5  POINT (-76.83450 39.04990)
3047  39.042000 -77.605400      4  POINT (-77.60540 39.04200)
3075  38.806200 -76.875600     25  POINT (-76.87560 38.80620)
3079  38.837700 -76.798000     14  POINT (-76.79800 38.83770)

To confirm we are collecting the correct points lets plot them on a new map along with the centroid of the convex hull. 


In [12]:
map = folium.Map(location = [38.9170, -77.0505], tiles='cartodbdark_matter' , zoom_start = 10)
folium.GeoJson(hull).add_to(map)
for x in pointsOnEdge.index:
    folium.CircleMarker(
                location=[locations['lat'][x], locations['lon'][x]],
                popup=locations['count'][x],
                radius = 1,
                color = 'red'
                ).add_to(map)

folium.CircleMarker(location=[poly_hull.centroid.y,poly_hull.centroid.x],radius =1).add_to(map)
map



Next we want to calculate the the distances between each of the points on the edge of the hull and the center. The greatest of these values will be our smallest covering circle. 

However since we want to obtain the radius in miles, we will convert to UTM coordinate system for our respective area which allows for accurate distance calculations 

In [22]:
#This function was taken from https://stackoverflow.com/questions/40132542/get-a-cartesian-projection-accurate-around-a-lat-lng-pair/40140326#40140326
def convert_wgs_to_utm(lon, lat):
    utm_band = str((math.floor((lon + 180) / 6 ) % 60) + 1)
    if len(utm_band) == 1:
        utm_band = '0'+utm_band
    if lat >= 0:
        epsg_code = '326' + utm_band
    else:
        epsg_code = '327' + utm_band
    return epsg_code
## Back to own code
utm_code =  convert_wgs_to_utm(poly_hull.centroid.x,poly_hull.centroid.y)
pointsOnEdge = pointsOnEdge.to_crs(utm_code)
pointsOnEdge

lat        lon  count                        geometry  \
2896  39.066800 -76.996900      2  POINT (327240.358 4326087.246)   
2955  38.976600 -76.805300     25  POINT (343618.964 4315729.797)   
3013  38.791200 -77.081400      1  POINT (319230.764 4295663.757)   
3024  38.815700 -77.621600     25  POINT (272386.136 4299590.234)   
3026  38.785562 -77.527546     11  POINT (280460.752 4296015.037)   
3037  39.049900 -76.834500      5  POINT (341253.409 4323915.425)   
3047  39.042000 -77.605400      4  POINT (274511.062 4324667.945)   
3075  38.806200 -76.875600     25  POINT (337140.082 4296941.605)   
3079  38.837700 -76.798000     14  POINT (343947.440 4300302.030)   

      distance to center  
2896        24440.808251  
2955        35693.141324  
3013        18559.141596  
3024        37568.508884  
3026        31443.418859  
3037        35532.301679  
3047        36569.217693  
3075        31944.364522  
3079        37131.129641

Finally we calculate the distances between all the edge points and the centre of the convex hull. 

In [23]:
center_data = [poly_hull.centroid for _ in pointsOnEdge.index]
center_data = gpd.GeoSeries(data = center_data,crs='epsg:4326').to_crs(utm_code)
distances = pointsOnEdge.distance(center_data,align=False)
pointsOnEdge['distance to center'] = distances
pointsOnEdge

lat        lon  count                        geometry  \
2896  39.066800 -76.996900      2  POINT (327240.358 4326087.246)   
2955  38.976600 -76.805300     25  POINT (343618.964 4315729.797)   
3013  38.791200 -77.081400      1  POINT (319230.764 4295663.757)   
3024  38.815700 -77.621600     25  POINT (272386.136 4299590.234)   
3026  38.785562 -77.527546     11  POINT (280460.752 4296015.037)   
3037  39.049900 -76.834500      5  POINT (341253.409 4323915.425)   
3047  39.042000 -77.605400      4  POINT (274511.062 4324667.945)   
3075  38.806200 -76.875600     25  POINT (337140.082 4296941.605)   
3079  38.837700 -76.798000     14  POINT (343947.440 4300302.030)   

      distance to center  
2896        24440.808251  
2955        35693.141324  
3013        18559.141596  
3024        37568.508884  
3026        31443.418859  
3037        35532.301679  
3047        36569.217693  
3075        31944.364522  
3079        37131.129641

We take the maximum distance as the radius of our circle.

In [25]:
radius = distances.max()
radius

37568.50888389839

Finally we create the smallest circle and plot it on a new map. 

In [28]:
smallest_series = gpd.GeoSeries(data = [poly_hull.centroid],crs= 'epsg:4326').to_crs(utm_code).buffer(radius)
smallest_circle = smallest_series.loc[0]

map = folium.Map(location = [38.9170, -77.0505], tiles='cartodbdark_matter' , zoom_start = 10)
folium.GeoJson(smallest_series).add_to(map)
map
